In [1]:
#For this analysis we will start off by gathering the information required from 
# wikipedia, Stats Canada, and foursquare


#Import Library to open URLs
import urllib.request
from bs4 import BeautifulSoup as bs

#import Pandas
import pandas as pd

##
#  WIKIPEDIA
##
#Website to scrap
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

#Open the url
page = urllib.request.urlopen(url)

#use soup
soup = bs(page,"lxml")

#print the results
#print(soup.prettify())

#all_tables = soup.find_all("table")
#all_tables

wiki_table = soup.find('table', class_='wikitable sortable')
wiki_table

#Scrap the columns and assign to a variable
pc = []
bo = []
nh = []

#create a fourloop to gather the requireed data
for row in wiki_table.findAll('tr'):
    cells=row.findAll('td')
    if len(cells)==3:
        pc.append(cells[0].find(text=True))
        bo.append(cells[1].find(text=True))
        nh.append(cells[2].find(text=True))

#use the fourloop to create the table
df = pd.DataFrame(pc,columns=["Postal Code"])
df["Borough"] = bo
df["Neighborhood"] = nh

#My table is bringing in dirty '\n' so here I am removing them
df = df.replace('\n', '',regex=True)

#Remove the Boroughs which are 'Not assigned'
df.drop(df.loc[df["Borough"] == 'Not assigned'].index, inplace=True)

In [2]:
# Check the table before moving on
df.head()

Postal Code           Borough                                 Neighborhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [3]:
# Use the downloadable GEO Coordinates from the link in week 3

#open CSV using pandas
data = pd.read_csv("/Users/admin/Desktop/Geospatial_Coordinates.csv")
#data.head()

#merge the information
df_latlong = df.merge(data,on='Postal Code')

#Check the table before moving on
df_latlong

Postal Code           Borough  \
0           M3A        North York   
1           M4A        North York   
2           M5A  Downtown Toronto   
3           M6A        North York   
4           M7A  Downtown Toronto   
..          ...               ...   
98          M8X         Etobicoke   
99          M4Y  Downtown Toronto   
100         M7Y      East Toronto   
101         M8Y         Etobicoke   
102         M8Z         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                            Parkwoods  43.753259 -79.329656  
1                                     Victoria Village  43.725882 -79.315572  
2                            Regent Park, Harbourfront  43.654260 -79.360636  
3                     Lawrence Manor, Lawrence Heights  43.718518 -79.464763  
4          Queen's Park, Ontario Provincial Government  43.662301 -79.389494  
..                                                 ...        ...        ...  
98       The Kingsway, Montgomery Road, Old Mill North  43.653654 -79.506944  
99                                Church and Wellesley  43.665860 -79.383160  
100  Business reply mail Processing Centre, South C...  43.662744 -79.321558  
101  Old Mill South, King's Mill Park, Sunnylea, Hu...  43.636258 -79.498509  
102  Mimico NW, The Queensway West, South of Bloor,...  43.628841 -79.520999  

[103 rows x 5 columns]

In [4]:
#I followed along with the last lab and completed a similar analysis and clustering of Toronto

#DOWNLOAD ALL DEPENDECIES
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Solving environment: done

# All requested packages already installed.

Libraries imported.


In [5]:
#Check the table

data.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [6]:

#Get the Lat Long for Toronto
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="to_explorer")
location = geolocator.geocode(address)

latitude = location.latitude
longitude = location.longitude
print('Torontos coordinates are {}, {}.'.format(latitude,longitude))

Torontos coordinates are 43.6534817, -79.3839347.


In [7]:
#Create a map of Toronto
map_toronto = folium.Map(location=[latitude,longitude],zoom_start=10)

#add markers to map
for lat, long, pc, borough, neighborhood in zip(df_latlong['Latitude'], df_latlong['Longitude'], df_latlong['Postal Code'], df_latlong['Borough'],df_latlong['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, long],
        radius=5,
        pupul=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)
    
map_toronto

In [8]:
# Define the Foursquare Credentials and Version
CLIENT_ID = 'VORXCA30A2XMAOUFI3DNVIEAHIVW2B2SKTXW4VLQBSRO3LEC' # your Foursquare ID
CLIENT_SECRET = 'HEYDELTJGSRVBGAWOHG44TS5AB10XD3IA1EHLPK0XJCIHZTI' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

nb_lat = df_latlong.loc[0, 'Latitude']
nb_long = df_latlong.loc[0, 'Longitude']
nb_name = df_latlong.loc[0, 'Neighborhood']

print('Latitude and longitude values of {} are {}, {}.'.format(nb_name, 
                                                               nb_lat, 
                                                               nb_long))
#Lets gather 50 venues within a 2000 meter radius from the center of the Neighborhood

LIMIT = 50
RADIUS = 2000
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    nb_lat, 
    nb_long, 
    RADIUS, 
    LIMIT)
url

Your credentails:
CLIENT_ID: VORXCA30A2XMAOUFI3DNVIEAHIVW2B2SKTXW4VLQBSRO3LEC
CLIENT_SECRET:HEYDELTJGSRVBGAWOHG44TS5AB10XD3IA1EHLPK0XJCIHZTI
Latitude and longitude values of Parkwoods are 43.7532586, -79.3296565.


'https://api.foursquare.com/v2/venues/explore?&client_id=VORXCA30A2XMAOUFI3DNVIEAHIVW2B2SKTXW4VLQBSRO3LEC&client_secret=HEYDELTJGSRVBGAWOHG44TS5AB10XD3IA1EHLPK0XJCIHZTI&v=20180605&ll=43.7532586,-79.3296565&radius=2000&limit=50'

In [9]:
#Check the results
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5edc2716e826ac001b7ad42a'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Parkwoods - Donalda',
  'headerFullLocation': 'Parkwoods - Donalda, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 91,
  'suggestedBounds': {'ne': {'lat': 43.77125861800002,
    'lng': -79.30478345939711},
   'sw': {'lat': 43.735258581999986, 'lng': -79.35452954060288}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4b8991cbf964a520814232e3',
       'name': "Allwyn's Bakery",
       'location': {'address': '81 Underhill drive',
        'lat': 43.75984035203157,
        'lng': -79.32471879917513,
        'labeledLatLngs': [{'label': 'display'

In [10]:
#CLEAN UP THE DATA
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']
    #Create a Dataframe to save the venues

venues = results['response']['groups'][0]['items']
    
nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

#Display the DF
nearby_venues

name  \
0                                Allwyn's Bakery   
1                    Donalda Golf & Country Club   
2                                Brookbanks Park   
3                                   Island Foods   
4                           Galleria Supermarket   
5                                           LCBO   
6                             Graydon Hall Manor   
7                             The Captain's Boil   
8                       Me Va Me Kitchen Express   
9                                  Baretto Caffé   
10         North Beach Indoor Volleyball Academy   
11                                   Casa Manila   
12                                    LA Fitness   
13                                   Tim Hortons   
14                            Darband Restaurant   
15                Shooters Snooker & Sports Club   
16                                Georgy Porgy's   
17                                           A&W   
18                            David Duncan House   
19         Matsuda Japanese Cuisine & Teppanyaki   
20                                Baskin-Robbins   
21                                     Dollarama   
22                                   Tim Hortons   
23                                       Gilaneh   
24                                       Freshii   
25                             Bruno's valu-mart   
26                                     Pizzaiolo   
27  GoodLife Fitness North York Victoria Terrace   
28                                       Paisano   
29                                 China Cottage   
30                     Popeyes Louisiana Kitchen   
31                                     Starbucks   
32                      Omni Palace Noodle House   
33                               The Bean Sprout   
34                                   Tim Hortons   
35                            Aroma Espresso Bar   
36                                       Staples   
37                                   Gonoe Sushi   
38                                   Tim Hortons   
39                                     Five Guys   
40                                   Food Basics   
41                                        Subway   
42                                   Thai One On   
43                               TD Canada Trust   
44                    The Westin Prince, Toronto   
45                      High Street Fish & Chips   
46                            Shoppers Drug Mart   
47                            Shoppers Drug Mart   
48                                The Beer Store   
49                                   Pizza Pizza   

                       categories        lat        lng  
0            Caribbean Restaurant  43.759840 -79.324719  
1                     Golf Course  43.752816 -79.342741  
2                            Park  43.751976 -79.332140  
3            Caribbean Restaurant  43.745866 -79.346035  
4                     Supermarket  43.753520 -79.349518  
5                    Liquor Store  43.757774 -79.314257  
6                     Event Space  43.763923 -79.342961  
7              Seafood Restaurant  43.754986 -79.349524  
8        Mediterranean Restaurant  43.754957 -79.351894  
9                            Café  43.744456 -79.346460  
10           Gym / Fitness Center  43.737191 -79.323714  
11            Filipino Restaurant  43.755277 -79.348873  
12           Gym / Fitness Center  43.747665 -79.347077  
13                           Café  43.760668 -79.326368  
14      Middle Eastern Restaurant  43.755194 -79.348498  
15                      Pool Hall  43.742637 -79.313052  
16            American Restaurant  43.741668 -79.314625  
17           Fast Food Restaurant  43.760643 -79.326865  
18                     Steakhouse  43.758259 -79.348886  
19            Japanese Restaurant  43.745494 -79.345821  
20                 Ice Cream Shop  43.742158 -79.314141  
21                 Discount Store  43.758135 -79.310672  
22                    Coffee Shop  43.752814 -79.314067  

In [11]:
def getNearbyVenues(names, latitudes, longitudes, radius=2000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)
to_venues = getNearbyVenues(names=df_latlong['Neighborhood'],
                            latitudes=df_latlong['Latitude'],
                            longitudes=df_latlong['Longitude'])

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [12]:
print(to_venues.shape)
to_venues.head()

(4979, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods              43.753259              -79.329656   
1    Parkwoods              43.753259              -79.329656   
2    Parkwoods              43.753259              -79.329656   
3    Parkwoods              43.753259              -79.329656   
4    Parkwoods              43.753259              -79.329656   

                         Venue  Venue Latitude  Venue Longitude  \
0              Allwyn's Bakery       43.759840       -79.324719   
1  Donalda Golf & Country Club       43.752816       -79.342741   
2              Brookbanks Park       43.751976       -79.332140   
3                 Island Foods       43.745866       -79.346035   
4         Galleria Supermarket       43.753520       -79.349518   

         Venue Category  
0  Caribbean Restaurant  
1           Golf Course  
2                  Park  
3  Caribbean Restaurant  
4           Supermarket

In [13]:
to_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                              50   
Alderwood, Long Branch                                                 50   
Bathurst Manor, Wilson Heights, Downsview North                        50   
Bayview Village                                                        50   
Bedford Park, Lawrence Manor East                                      50   
Berczy Park                                                            50   
Birch Cliff, Cliffside West                                            47   
Brockton, Parkdale Village, Exhibition Place                           50   
Business reply mail Processing Centre, South Ce...                     50   
CN Tower, King and Spadina, Railway Lands, Harb...                     50   
Caledonia-Fairbanks                                                    50   
Canada Post Gateway Processing Centre                                  50   
Cedarbrae                                                              50   
Central Bay Street                                                     50   
Christie                                                               50   
Church and Wellesley                                                   50   
Clarks Corners, Tam O'Shanter, Sullivan                                50   
Cliffside, Cliffcrest, Scarborough Village West                        37   
Commerce Court, Victoria Hotel                                         50   
Davisville                                                             50   
Davisville North                                                       50   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                       50   
Don Mills                                                             100   
Dorset Park, Wexford Heights, Scarborough Town ...                     50   
Downsview                                                             178   
Dufferin, Dovercourt Village                                           50   
East Toronto, Broadview North (Old East York)                          50   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                     33   
Fairview, Henry Farm, Oriole                                           50   
First Canadian Place, Underground city                                 50   
Forest Hill North & West, Forest Hill Road Park                        50   
Garden District, Ryerson                                               50   
Glencairn                                                              50   
Golden Mile, Clairlea, Oakridge                                        50   
Guildwood, Morningside, West Hill                                      42   
Harbourfront East, Union Station, Toronto Islands                      50   
High Park, The Junction South                                          50   
Hillcrest Village                                                      50   
Humber Summit                                                          26   
Humberlea, Emery                                                       48   
Humewood-Cedarvale                                                     50   
India Bazaar, The Beaches West                                         50   
Islington Avenue, Humber Valley Village                                49   
Kennedy Park, Ionview, East Birchmount Park                            50   
Kensington Market, Chinatown, Grange Park                              50   
Kingsview Village, St. Phillips, Martin Grove G...                     50   
Lawrence Manor, Lawrence Heights                                       50   
Lawrence Park                                                          50   
Leaside                                                                50   
Little Portugal, Trinity                                               50   
Malvern, Rouge                                  

In [14]:
#Analyze the Neighborhoods
# one hot encoding
to_onehot = pd.get_dummies(to_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhood'] = to_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

to_onehot.head()

Zoo Exhibit  Afghan Restaurant  Airport  Airport Lounge  \
0            0                  0        0               0   
1            0                  0        0               0   
2            0                  0        0               0   
3            0                  0        0               0   
4            0                  0        0               0   

   American Restaurant  Amphitheater  Antique Shop  Aquarium  Art Gallery  \
0                    0             0             0         0            0   
1                    0             0             0         0            0   
2                    0             0             0         0            0   
3                    0             0             0         0            0   
4                    0             0             0         0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Bath House  Beach  \
0               0                 0                   0           0      0   
1               0                 0                   0           0      0   
2               0                 0                   0           0      0   
3               0                 0                   0           0      0   
4               0                 0                   0           0      0   

   Beer Bar  Beer Store  Big Box Store  Bike Shop  Bistro  Bookstore  \
0         0           0              0          0       0          0   
1         0           0              0          0       0          0   
2         0           0              0          0       0          0   
3         0           0              0          0       0          0   
4         0           0              0          0       0          0   

   Botanical Garden  Boutique  Bowling Alley  Brazilian Restaurant  \
0                 0         0              0                     0   
1                 0         0              0                     0   
2                 0         0              0                     0   
3                 0         0              0                     0   
4                 0         0              0                     0   

   Breakfast Spot  Brewery  Bridal Shop  Bubble Tea Shop  Burger Joint  \
0               0        0            0                0             0   
1               0        0            0                0             0   
2               0        0            0                0             0   
3               0        0            0                0             0   
4               0        0            0                0             0   

   Burrito Place  Bus Line  Bus Station  Bus Stop  Butcher  Café  \
0              0         0            0         0        0     0   
1              0         0            0         0        0     0   
2              0         0            0         0        0     0   
3              0         0            0         0        0     0   
4              0         0            0         0        0     0   

   Camera Store  Cantonese Restaurant  Caribbe

In [15]:
#Group the rows by Neighborhood, and get the mean frequency of occurance of each category
to_grouped = to_onehot.groupby('Neighborhood').mean().reset_index()
to_grouped

Neighborhood  Zoo Exhibit  \
0                                           Agincourt         0.00   
1                              Alderwood, Long Branch         0.00   
2     Bathurst Manor, Wilson Heights, Downsview North         0.00   
3                                     Bayview Village         0.00   
4                   Bedford Park, Lawrence Manor East         0.00   
5                                         Berczy Park         0.00   
6                         Birch Cliff, Cliffside West         0.00   
7        Brockton, Parkdale Village, Exhibition Place         0.00   
8   Business reply mail Processing Centre, South C...         0.00   
9   CN Tower, King and Spadina, Railway Lands, Har...         0.00   
10                                Caledonia-Fairbanks         0.00   
11              Canada Post Gateway Processing Centre         0.00   
12                                          Cedarbrae         0.00   
13                                 Central Bay Street         0.00   
14                                           Christie         0.00   
15                               Church and Wellesley         0.00   
16            Clarks Corners, Tam O'Shanter, Sullivan         0.00   
17    Cliffside, Cliffcrest, Scarborough Village West         0.00   
18                     Commerce Court, Victoria Hotel         0.00   
19                                         Davisville         0.00   
20                                   Davisville North         0.00   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn         0.00   
22                                          Don Mills         0.00   
23  Dorset Park, Wexford Heights, Scarborough Town...         0.00   
24                                          Downsview         0.00   
25                       Dufferin, Dovercourt Village         0.00   
26      East Toronto, Broadview North (Old East York)         0.00   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...         0.00   
28                       Fairview, Henry Farm, Oriole         0.00   
29             First Canadian Place, Underground city         0.00   
30    Forest Hill North & West, Forest Hill Road Park         0.00   
31                           Garden District, Ryerson         0.00   
32                                          Glencairn         0.00   
33                    Golden Mile, Clairlea, Oakridge         0.00   
34                  Guildwood, Morningside, West Hill         0.00   
35  Harbourfront East, Union Station, Toronto Islands         0.00   
36                      High Park, The Junction South         0.00   
37                                  Hillcrest Village         0.00   
38                                      Humber Summit         0.00   
39                                   Humberlea, Emery         0.00   
40                                 Humewood-Cedarvale         0.00   
41                     India Bazaar, The Beaches West         0.00   
42            Islington Avenue, Humber Valley Village         0.00   
43        Kennedy Park, Ionview, East Birchmount Park         0.00   
44          Kensington Market, Chinatown, Grange Park         0.00   
45  Kingsview Village, St. Phillips, Martin Grove ...         0.00   
46                   Lawrence Manor, Lawrence Heights         0.00   
47                                      Lawrence Park         0.00   
48                                            Leaside         0.00   
49                           Little Portugal, Trinity         0.00   
50                                     Malvern, Rouge         0.32   
51  Milliken, Agincourt North, Steeles East, L'Amo...         0.00   
52  Mimico NW, The Queensway West, South of Bloor,...         0.00   
53                        Moore Park, Summerhill East         0.00   
54       New Toronto, Mimico South, Humber Bay Shores         0.00   
55           North Park, Maple Leaf Park, Upwood Park         0.00   
56                 North Toronto West,  Lawrence Pa

In [16]:
#Open the CSV I created based on the venues from Foursquare to match the NAICS values for Stat Canada
fs_naics = pd.read_csv("/Users/admin/Desktop/foursquare_naics.csv")
fs_naics.head()

Venue Category  NAICS
0          Zoo Exhibit     71
1    Afghan Restaurant     72
2   African Restaurant     72
3              Airport     48
4  American Restaurant     72

In [17]:
#Open the CSV I created based on the Categories found by foursquare to match them to the NAICS values
stats_can = pd.read_csv("/Users/admin/Desktop/layoffs_statscanada.csv")
stats_can.head()

NAICS                                           Name  percent
0     11     Agriculture, Forestry, Fishing and Hunting     23.6
1     21  Mining, Quarrying, and Oil and Gas Extraction     26.9
2     22                                      Utilities     26.7
3     23                                   Construction     41.6
4     31                                  Manufacturing     29.4

In [18]:
#Merge the tables I created together
can_naics = stats_can.merge(fs_naics,on='NAICS')
can_naics.head()

NAICS             Name  percent       Venue Category
0     42  Wholesale Trade     24.6  Distribution Center
1     42  Wholesale Trade     24.6                 Farm
2     42  Wholesale Trade     24.6       Farmers Market
3     42  Wholesale Trade     24.6          Fish Market
4     42  Wholesale Trade     24.6          Flea Market

In [19]:
#Merge the Dataframes I created based on Stats Canada and NAICS code information
# with the to_grouped dataframe

to_venue_naics = can_naics.merge(to_venues,on='Venue Category')
to_venue_naics

NAICS                                              Name  percent  \
0        42                                   Wholesale Trade     24.6   
1        42                                   Wholesale Trade     24.6   
2        42                                   Wholesale Trade     24.6   
3        42                                   Wholesale Trade     24.6   
4        42                                   Wholesale Trade     24.6   
5        42                                   Wholesale Trade     24.6   
6        42                                   Wholesale Trade     24.6   
7        42                                   Wholesale Trade     24.6   
8        42                                   Wholesale Trade     24.6   
9        42                                   Wholesale Trade     24.6   
10       42                                   Wholesale Trade     24.6   
11       42                                   Wholesale Trade     24.6   
12       42                                   Wholesale Trade     24.6   
13       42                                   Wholesale Trade     24.6   
14       42                                   Wholesale Trade     24.6   
15       42                                   Wholesale Trade     24.6   
16       42                                   Wholesale Trade     24.6   
17       42                                   Wholesale Trade     24.6   
18       42                                   Wholesale Trade     24.6   
19       42                                   Wholesale Trade     24.6   
20       42                                   Wholesale Trade     24.6   
21       42                                   Wholesale Trade     24.6   
22       42                                   Wholesale Trade     24.6   
23       42                                   Wholesale Trade     24.6   
24       42                                   Wholesale Trade     24.6   
25       42                                   Wholesale Trade     24.6   
26       42                                   Wholesale Trade     24.6   
27       42                                   Wholesale Trade     24.6   
28       42                                   Wholesale Trade     24.6   
29       42                                   Wholesale Trade     24.6   
30       42                                   Wholesale Trade     24.6   
31       42                                   Wholesale Trade     24.6   
32       42                                   Wholesale Trade     24.6   
33       42                                   Wholesale Trade     24.6   
34       42                                   Wholesale Trade     24.6   
35       42                                   Wholesale Trade     24.6   
36       42                                   Wholesale Trade     24.6   
37       42                                   Wholesale Trade     24.6   
38       42                                   Wholesale Trade     24.6   
39       42                                   Wholesale Trade     24.6   
40       42                                   Wholesale Trade     24.6   
41       42                                   Wholesale Trade     24.6   
42       42                                   Wholesale Trade     24.6   
43       42                                   Wholesale Trade     24.6   
44       42                                   Wholesale Trade     24.6   
45       42                                   Wholesale Trade     24.6   
46       42                                   Wholesale Trade     24.6   
47       42                                   Wholesale Trade     24.6   
48       42                                   Wholesale Trade     24.6   
49       42                                   Wholesale Trade     24.6   
50       42                                   Wholesale Trade     24.6   
51       42                                   Wholesale Trade     24.6   
52       42                                   Wholesale Trade     24.6   
53       4

In [20]:
#Create the dataframe that will be used to see which neighbourhoods are hit the most
pc = []

Can_layoffs = pd.DataFrame(pc,columns=["Neighbourhood","Lost jobs"])
Can_layoffs

Empty DataFrame
Columns: [Neighbourhood, Lost jobs]
Index: []

In [22]:
#Print the Neighborhood with the top 10 venues

num_top_venues = 10
Total = 0

for hood in to_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = to_grouped[to_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    #Add the information I wish to see in the table here
    temp['NACIS'] = to_venue_naics['NAICS']
    temp['Percent'] = to_venue_naics['percent']
    temp['Sum'] = (temp['freq'].astype(float) * (to_venue_naics['percent']/100))
                                                 
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')
    #Use code to add up the sum                                            
    print('Out of the top 10 business categories in this neighbourhood ', round((100 * temp['Sum']).sum(),2), '%\nof them laid off 80% or more of their staff')
    print('\n')
 
    #Append the DF to add the neighbourhoods up to be used                                       
    Can_layoffs = Can_layoffs.append(pd.Series([hood , round((100 * temp['Sum']).sum(),2)], index=Can_layoffs.columns), ignore_index=True )
    

----Agincourt----
                  venue  freq  NACIS  Percent      Sum
0    Chinese Restaurant  0.10     42     24.6  0.02460
1     Indian Restaurant  0.06     44     51.2  0.03072
2              Pharmacy  0.06     44     51.2  0.03072
3        Breakfast Spot  0.04     42     24.6  0.00984
4  Caribbean Restaurant  0.04     42     24.6  0.00984
5        Sandwich Place  0.04     44     51.2  0.02048
6  Gym / Fitness Center  0.04     44     51.2  0.02048
7                Bakery  0.04     42     24.6  0.00984
8      Sushi Restaurant  0.04     44     51.2  0.02048
9            Restaurant  0.04     44     51.2  0.02048


Out of the top 10 business categories in this neighbourhood  43.22 %
of them laid off 80% or more of their staff


----Alderwood, Long Branch----
                  venue  freq  NACIS  Percent      Sum
0           Coffee Shop  0.06     44     51.2  0.03072
1    Seafood Restaurant  0.06     44     51.2  0.03072
2           Pizza Place  0.04     44     51.2  0.02048
3        

In [23]:
#Arrange the DF in a usable format
Can_layoffs.sort_values(by='Lost jobs', ascending=True)

Neighbourhood  Lost jobs
50                                     Malvern, Rouge      40.03
75                      Steeles West, L'Amoreaux West      40.56
34                  Guildwood, Morningside, West Hill      40.72
41                     India Bazaar, The Beaches West      41.09
4                   Bedford Park, Lawrence Manor East      41.09
49                           Little Portugal, Trinity      41.62
80                                        The Beaches      41.62
8   Business reply mail Processing Centre, South C...      41.66
26      East Toronto, Broadview North (Old East York)      42.16
70                      Runnymede, The Junction North      42.16
10                                Caledonia-Fairbanks      42.16
37                                  Hillcrest Village      42.16
25                       Dufferin, Dovercourt Village      42.16
44          Kensington Market, Chinatown, Grange Park      42.69
36                      High Park, The Junction South      42.69
60                             Parkdale, Roncesvalles      42.69
77                                    Studio District      42.73
93                        Willowdale, Willowdale East      42.87
0                                           Agincourt      43.22
11              Canada Post Gateway Processing Centre      43.22
6                         Birch Cliff, Cliffside West      43.30
54       New Toronto, Mimico South, Humber Bay Shores      43.75
81                       The Danforth West, Riverdale      43.75
51  Milliken, Agincourt North, Steeles East, L'Amo...      43.75
52  Mimico NW, The Queensway West, South of Bloor,...      43.75
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn      43.75
96                                   Woodbine Heights      43.75
23  Dorset Park, Wexford Heights, Scarborough Town...      43.75
13                                 Central Bay Street      43.79
29             First Canadian Place, Underground city      43.83
22                                          Don Mills      44.02
48                                            Leaside      44.28
16            Clarks Corners, Tam O'Shanter, Sullivan      44.28
7        Brockton, Parkdale Village, Exhibition Place      44.28
40                                 Humewood-Cedarvale      44.28
85                     University of Toronto, Harbord      44.32
43        Kennedy Park, Ionview, East Birchmount Park      44.82
3                                     Bayview Village      44.82
30    Forest Hill North & West, Forest Hill Road Park      44.82
35  Harbourfront East, Union Station, Toronto Islands      44.86
33                    Golden Mile, Clairlea, Oakridge      45.35
91                                  Wexford, Maryvale      45.35
71                                Scarborough Village      45.35
28                       Fairview, Henry Farm, Oriole      45.35
69                                 Runnymede, Swansea      45.35
78  Summerhill West, Rathnelly, South Hill, Forest...      45.35
42            Islington Avenue, Humber Valley Village      45.39
31                           Garden District, Ryerson      45.39
9   CN Tower, King and Spadina, Railway Lands, Har...      45.39
39                                   Humberlea, Emery      45.43
18                     Commerce Court, Victoria Hotel      45.43
84           Toronto Dominion Centre, Design Exchange      45.43
68             Rouge Hill, Port Union, Highland Creek      45.57
38                                      Humber Summit      45.80
19                                         Davisville      45.88
82      The Kingsway, Montgomery Road, Old Mill North      45.88
83                                   Thorncliffe Park      45.88
92                            Willowdale, Newtonbrook      45.88
94                        Willowdale, Willowdale West      45.88
95                                             Woburn      45.88
2     Bathurst Manor, Wilson Heights, Downsview North      45.88
67        

In [24]:
#I must re-name a column header 
Can_layoffs.rename(columns={'Neighbourhood':'Neighborhood'}, 
                 inplace=True)
Can_layoffs.sort_values(by='Lost jobs', ascending=True)

Neighborhood  Lost jobs
50                                     Malvern, Rouge      40.03
75                      Steeles West, L'Amoreaux West      40.56
34                  Guildwood, Morningside, West Hill      40.72
41                     India Bazaar, The Beaches West      41.09
4                   Bedford Park, Lawrence Manor East      41.09
49                           Little Portugal, Trinity      41.62
80                                        The Beaches      41.62
8   Business reply mail Processing Centre, South C...      41.66
26      East Toronto, Broadview North (Old East York)      42.16
70                      Runnymede, The Junction North      42.16
10                                Caledonia-Fairbanks      42.16
37                                  Hillcrest Village      42.16
25                       Dufferin, Dovercourt Village      42.16
44          Kensington Market, Chinatown, Grange Park      42.69
36                      High Park, The Junction South      42.69
60                             Parkdale, Roncesvalles      42.69
77                                    Studio District      42.73
93                        Willowdale, Willowdale East      42.87
0                                           Agincourt      43.22
11              Canada Post Gateway Processing Centre      43.22
6                         Birch Cliff, Cliffside West      43.30
54       New Toronto, Mimico South, Humber Bay Shores      43.75
81                       The Danforth West, Riverdale      43.75
51  Milliken, Agincourt North, Steeles East, L'Amo...      43.75
52  Mimico NW, The Queensway West, South of Bloor,...      43.75
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn      43.75
96                                   Woodbine Heights      43.75
23  Dorset Park, Wexford Heights, Scarborough Town...      43.75
13                                 Central Bay Street      43.79
29             First Canadian Place, Underground city      43.83
22                                          Don Mills      44.02
48                                            Leaside      44.28
16            Clarks Corners, Tam O'Shanter, Sullivan      44.28
7        Brockton, Parkdale Village, Exhibition Place      44.28
40                                 Humewood-Cedarvale      44.28
85                     University of Toronto, Harbord      44.32
43        Kennedy Park, Ionview, East Birchmount Park      44.82
3                                     Bayview Village      44.82
30    Forest Hill North & West, Forest Hill Road Park      44.82
35  Harbourfront East, Union Station, Toronto Islands      44.86
33                    Golden Mile, Clairlea, Oakridge      45.35
91                                  Wexford, Maryvale      45.35
71                                Scarborough Village      45.35
28                       Fairview, Henry Farm, Oriole      45.35
69                                 Runnymede, Swansea      45.35
78  Summerhill West, Rathnelly, South Hill, Forest...      45.35
42            Islington Avenue, Humber Valley Village      45.39
31                           Garden District, Ryerson      45.39
9   CN Tower, King and Spadina, Railway Lands, Har...      45.39
39                                   Humberlea, Emery      45.43
18                     Commerce Court, Victoria Hotel      45.43
84           Toronto Dominion Centre, Design Exchange      45.43
68             Rouge Hill, Port Union, Highland Creek      45.57
38                                      Humber Summit      45.80
19                                         Davisville      45.88
82      The Kingsway, Montgomery Road, Old Mill North      45.88
83                                   Thorncliffe Park      45.88
92                            Willowdale, Newtonbrook      45.88
94                        Willowdale, Willowdale West      45.88
95                                             Woburn      45.88
2     Bathurst Manor, Wilson Heights, Downsview North      45.88
67         

In [25]:
#Put the data into a Pandas Dataframe
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [26]:
#Create a df which displays the top 10 venues of each Neighborhood
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = to_grouped['Neighborhood']

for ind in np.arange(to_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(to_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue  \
0                                        Agincourt    Chinese Restaurant   
1                           Alderwood, Long Branch           Coffee Shop   
2  Bathurst Manor, Wilson Heights, Downsview North                  Park   
3                                  Bayview Village                  Park   
4                Bedford Park, Lawrence Manor East                Bakery   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0              Pharmacy     Indian Restaurant        Breakfast Spot   
1    Seafood Restaurant  Fast Food Restaurant      Department Store   
2           Coffee Shop           Pizza Place              Pharmacy   
3    Chinese Restaurant           Coffee Shop                  Bank   
4      Sushi Restaurant                   Pub           Coffee Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Restaurant      Sushi Restaurant                Bakery   
1           Pizza Place        Breakfast Spot                  Café   
2        Sandwich Place           Gas Station                  Bank   
3              Pharmacy        Clothing Store                  Café   
4            Bagel Shop  Fast Food Restaurant                  Café   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0           Gas Station  Caribbean Restaurant         Sandwich Place  
1           Wings Joint     Electronics Store             Restaurant  
2     Convenience Store            Restaurant          Deli / Bodega  
3         Grocery Store           Gas Station    Japanese Restaurant  
4    Italian Restaurant      Asian Restaurant            Sports Club

In [34]:
#Run K means to cluster the neighborhood into 5 clusters
# set number of clusters
kclusters = 5

to_grouped_clustering = to_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(to_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 


array([1, 2, 1, 1, 3, 2, 1, 2, 3, 2], dtype=int32)

In [36]:
#Create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

to_merged = df_latlong

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

to_merged.head() # check the last columns!

Postal Code           Borough                                 Neighborhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0  43.753259 -79.329656               1           Coffee Shop   
1  43.725882 -79.315572               1           Coffee Shop   
2  43.654260 -79.360636               2           Coffee Shop   
3  43.718518 -79.464763               2        Clothing Store   
4  43.662301 -79.389494               2            Comic Shop   

    2nd Most Common Venue 3rd Most Common Venue      4th Most Common Venue  \
0                Pharmacy           Supermarket        Japanese Restaurant   
1                     Gym         Grocery Store  Middle Eastern Restaurant   
2                    Park            Restaurant             Farmers Market   
3  Furniture / Home Store      Greek Restaurant      Vietnamese Restaurant   
4     Japanese Restaurant          Dance Studio                Coffee Shop   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0  Gym / Fitness Center           Pizza Place    Chinese Restaurant   
1            Beer Store  Gym / Fitness Center   Japanese Restaurant   
2               Brewery     French Restaurant            Taco Place   
3         Jewelry Store   Fried Chicken Joint            Restaurant   
4        Clothing Store            Restaurant       Bubble Tea Shop   

  8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
0  Caribbean Restaurant                  Café  Middle Eastern Restaurant  
1              Pharmacy        Ice Cream Shop          Indian Restaurant  
2                Garden        Clothing Store                     Circus  
3        Cosmetics Shop         Movie Theater                 Steakhouse  
4                  Park        Sandwich Place                Supermarket

In [37]:
#Merge the Table I created with theJob loss information
to_merged_job = Can_layoffs.merge(to_merged,on='Neighborhood')
to_merged_job

Neighborhood  Lost jobs Postal Code  \
0                                            Agincourt      43.22         M1S   
1                               Alderwood, Long Branch      46.94         M8W   
2      Bathurst Manor, Wilson Heights, Downsview North      45.88         M3H   
3                                      Bayview Village      44.82         M2K   
4                    Bedford Park, Lawrence Manor East      41.09         M5M   
5                                          Berczy Park      46.45         M5E   
6                          Birch Cliff, Cliffside West      43.30         M1N   
7         Brockton, Parkdale Village, Exhibition Place      44.28         M6K   
8    Business reply mail Processing Centre, South C...      41.66         M7Y   
9    CN Tower, King and Spadina, Railway Lands, Har...      45.39         M5V   
10                                 Caledonia-Fairbanks      42.16         M6E   
11               Canada Post Gateway Processing Centre      43.22         M7R   
12                                           Cedarbrae      45.88         M1H   
13                                  Central Bay Street      43.79         M5G   
14                                            Christie      46.94         M6G   
15                                Church and Wellesley      46.94         M4Y   
16             Clarks Corners, Tam O'Shanter, Sullivan      44.28         M1T   
17     Cliffside, Cliffcrest, Scarborough Village West      47.70         M1M   
18                      Commerce Court, Victoria Hotel      45.43         M5L   
19                                          Davisville      45.88         M4S   
20                                    Davisville North      46.94         M4P   
21    Del Ray, Mount Dennis, Keelsdale and Silverthorn      43.75         M6M   
22                                           Don Mills      44.02         M3B   
23                                           Don Mills      44.02         M3C   
24   Dorset Park, Wexford Heights, Scarborough Town...      43.75         M1P   
25                                           Downsview      54.11         M3K   
26                                           Downsview      54.11         M3L   
27                                           Downsview      54.11         M3M   
28                                           Downsview      54.11         M3N   
29                        Dufferin, Dovercourt Village      42.16         M6H   
30       East Toronto, Broadview North (Old East York)      42.16         M4J   
31   Eringate, Bloordale Gardens, Old Burnhamthorpe...      46.70         M9C   
32                        Fairview, Henry Farm, Oriole      45.35         M2J   
33              First Canadian Place, Underground city      43.83         M5X   
34     Forest Hill North & West, Forest Hill Road Park      44.82         M5P   
35                            Garden District, Ryerson      45.39         M5B   
36                                           Glencairn      46.94         M6B   
37                     Golden Mile, Clairlea, Oakridge      45.35         M1L   
38                   Guildwood, Morningside, West Hill      40.72         M1E   
39   Harbourfront East, Union Station, Toronto Islands      44.86         M5J   
40                       High Park, The Junction South      42.69         M6P   
41                                   Hillcrest Village      42.16         M2H   
42                                       Humber Summit      45.80         M9L   
43                                    Humberlea, Emery      45.43         M9M   
44                                  Humewood-Cedarvale      44.28         M6C   
45                      India Bazaar, The Beaches West      41.09         M4L   
46             Islington Avenue, Humber Valley Village      45.39         M9A   
47         Kennedy Park, Ionview, East Birchmount Park      44.82         M1K   
48           Kensington Market, Chinatown, Grange Park      42.69        

In [52]:
#Visualize the clustering
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster, los in zip(to_merged_job['Latitude'], to_merged_job['Longitude'], to_merged_job['Neighborhood'], to_merged_job['Cluster Labels'],to_merged_job['Lost jobs']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster) + ' Job Loss; ' + str(los) + '%', parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters